In [3]:
import torch
import torchvision.transforms as transforms
from torchvision.datasets import ImageFolder
from PIL import Image
import os

# Define the device
device = (
    "cuda"
    if torch.cuda.is_available()
    else "mps"
    if torch.backends.mps.is_available()
    else "cpu"
)

class Params:
    def __init__(self):
        self.batch_size = 512
        self.name = "resnet_50"
        self.workers = 16
        self.lr = 0.1
        self.momentum = 0.9
        self.weight_decay = 1e-4
        self.lr_step_size = 30
        self.lr_gamma = 0.1

    def __repr__(self):
        return str(self.__dict__)
    
    def __eq__(self, other):
        return self.__dict__ == other.__dict__
    
params = Params()

# Path to the saved model checkpoint
checkpoint_path = "checkpoints/resnet_50/checkpoint.pth"

# Load the model architecture
from model import ResNet50  # Assuming resnet.py contains your model definition

num_classes = 1000  # Adjust this to match your dataset
model = ResNet50(num_classes=num_classes).to(device)

# Load the trained model weights
checkpoint = torch.load(checkpoint_path)
model.load_state_dict(checkpoint["model"])

model.eval()

# Define transformations for inference
inference_transforms = transforms.Compose([
    transforms.ToTensor(),
    transforms.Resize(size=256),
    transforms.CenterCrop(224),
    transforms.Normalize(mean=[0.485, 0.485, 0.406], std=[0.229, 0.224, 0.225]),
])

# Function to make predictions on a single image
def predict(image_path, model, transforms, class_names=None):
    # Load and transform the image
    image = Image.open(image_path).convert("RGB")
    image_tensor = transforms(image).unsqueeze(0).to(device)

    # Forward pass
    with torch.no_grad():
        output = model(image_tensor)
        probabilities = torch.nn.functional.softmax(output[0], dim=0)
        top_prob, top_class = probabilities.topk(5, largest=True, sorted=True)

    # Display the top predictions
    print("Predictions:")
    for i in range(top_prob.size(0)):
        class_name = class_names[top_class[i]] if class_names else f"Class {top_class[i].item()}"
        print(f"{class_name}: {top_prob[i].item() * 100:.2f}%")

    return top_prob, top_class

# Define the dataset class names if available (optional)
# Example: Load class names from the training dataset folder
dataset_path = 'Imagenet/ILSVRC/Data/CLS-LOC/train'
class_names = sorted(os.listdir(dataset_path))

# Path to the image for inference
image_path = "dog.png"  # Replace with the actual path to your test image

# Make a prediction
predict(image_path, model, inference_transforms, class_names=class_names)


/tmp/ipykernel_312819/875621319.py:45: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  checkpoint = torch.load(checkpoint_path)


Predictions:
n02105412: 26.26%
n02106662: 14.42%
n02099601: 8.62%
n02105162: 7.17%
n02105251: 3.21%


(tensor([0.2626, 0.1442, 0.0862, 0.0717, 0.0321], device='cuda:0'),
 tensor([227, 235, 207, 225, 226], device='cuda:0'))

In [4]:
# Path to the class mapping text file
class_mapping_file = "Imagenet/LOC_synset_mapping.txt"  # Replace with the actual path

# Read the file and create a mapping
id_to_name = {}
with open(class_mapping_file, 'r') as f:
    for line in f:
        class_id, class_name = line.strip().split(" ", 1)
        id_to_name[class_id] = class_name

# Model output (example)
predicted_ids = ["n02105412", "n02106662", "n02099601", "n02105162", "n02105251"]
probabilities = [26.26, 14.42, 8.62, 7.17, 3.21]

# Map the IDs to their names
predicted_names = [id_to_name[class_id] for class_id in predicted_ids]

# Display the predictions
print("Predictions:")
for prob, name in zip(probabilities, predicted_names):
    print(f"{name}: {prob:.2f}%")


Predictions:
kelpie: 26.26%
German shepherd, German shepherd dog, German police dog, alsatian: 14.42%
golden retriever: 8.62%
malinois: 7.17%
briard: 3.21%
